In [13]:
import sqlite3
import os
import pandas as pd

# dataset = r'D:\liurui\dev\code\PriceForecast\yuanyoudataset'

dataset = r'C:\Users\Administrator\Desktop'    

# 预测价格数据
# dbfilename = os.path.join(r'D:\code\PriceForecast\yuanyoudataset','jbsh_yuanyou.db')
# conn = sqlite3.connect(dbfilename)
# query = 'SELECT * FROM accuracy'
# df1 = pd.read_sql_query(query, conn)
# df1['ds'] =  df1['PREDICT_DATE']
# conn.close()
# print(df1.shape)

# 预测价格数据
dfcsvfilename = os.path.join(dataset,'accuracy_ten.csv')
df1 = pd.read_csv(dfcsvfilename)
print(df1.shape)

# 最高最低价
xlsfilename = os.path.join(dataset,'数据项下载.xls')
df2 = pd.read_excel(xlsfilename)[5:]
df2 = df2.rename(columns = {'数据项名称':'ds','布伦特最低价':'LOW_PRICE','布伦特最高价':'HIGH_PRICE'})
print(df2.shape)



df = pd.merge(df1,df2,on=['ds'],how='left')

df['ds'] =  pd.to_datetime(df['ds'])
# df['PREDICT_DATE'] =  pd.to_datetime(df['PREDICT_DATE'])
df = df.reindex()

print(df.shape)
# from datetime import datetime
import time
df.to_csv(os.path.join(dataset,f'预测数据-{time.time()}.csv'))
# df = df[['ds','min_within_quantile','max_within_quantile']]



# 打印数据框的前几行
print(df.head())
print(df.tail())


(85, 28)
(22, 4)
(85, 31)
          ds      NHITS   Informer       LSTM  iTransformer   TSMixer  \
0 2024-11-25  75.714300  75.523370  73.614220      75.27068  75.03936   
1 2024-11-26  76.039635  75.558270  73.692310      75.04110  74.60100   
2 2024-11-27  77.375790  75.361885  73.826140      74.99121  74.37731   
3 2024-11-28  78.872400  76.339920  73.883484      75.79425  74.04826   
4 2024-11-29  79.576970  76.333170  73.876396      75.89008  74.07330   

    TSMixerx  PatchTST        RNN        GRU  ...          y  \
0  74.581190  75.70277  74.721280  74.512060  ...  73.010002   
1  73.496025  75.97611  74.588060  74.713425  ...  72.809998   
2  73.522026  76.48628  74.486400  74.946010  ...  72.830002   
3  73.416306  76.38267  75.195710  74.946014  ...  73.279999   
4  73.521570  76.20661  75.089966  74.935165  ...  72.940002   

   min_within_quantile  max_within_quantile  id  CREAT_DATE  min_price  \
0             74.41491             75.29100   1  2024-11-22  74.414910   
1 

In [27]:
# 模型评估前五均值      
df['min_price'] = df.iloc[:,1:11].mean(axis=1) -2
df['max_price'] = df.iloc[:,1:11].mean(axis=1) +2

In [28]:
# 定义一个函数来计算准确率
# 比较真实最高最低，和预测最高最低 计算准确率
def calculate_accuracy(row):
    # 全子集情况：
    if (row['max_price'] >= row['HIGH_PRICE'] and row['min_price'] <= row['LOW_PRICE']) or \
        (row['max_price'] <= row['HIGH_PRICE'] and row['min_price'] >= row['LOW_PRICE']):
        return 1    
    # 无交集情况：
    if row['max_price'] < row['LOW_PRICE'] or \
        row['min_price'] > row['HIGH_PRICE']:
        return 0
    # 有交集情况：
    else:
        sorted_prices = sorted([row['LOW_PRICE'], row['min_price'], row['max_price'], row['HIGH_PRICE']])
        middle_diff = sorted_prices[2] - sorted_prices[1]
        price_range = row['HIGH_PRICE'] - row['LOW_PRICE']
        accuracy = middle_diff / price_range
        return accuracy
import datetime
weight_dict = [0.4,0.15,0.1,0.1,0.25] # 权重

columns = ['HIGH_PRICE','LOW_PRICE','min_price','max_price']
df[columns] = df[columns].astype(float)
df['ACCURACY'] = df.apply(calculate_accuracy, axis=1)
# df['ACCURACY'] = df.apply(is_within_range, axis=1)
# 取结束日期上一周的日期
def get_week_date(end_time):
    endtime = end_time
    endtimeweek = datetime.datetime.strptime(endtime, '%Y-%m-%d')
    up_week = endtimeweek - datetime.timedelta(days=endtimeweek.weekday() + 14)
    up_week_dates = [up_week + datetime.timedelta(days=i) for i in range(14)][4:-2]
    up_week_dates = [date.strftime('%Y-%m-%d') for date in up_week_dates]
    return up_week_dates

# 计算准确率并保存结果
def _get_accuracy_rate(df,up_week_dates,endtime):
    df3 = df.copy()
    df3 = df3[df3['CREAT_DATE'].isin(up_week_dates)]
    df3 = df3[df3['ds'].isin(up_week_dates)]
    accuracy_rote = 0
    for i,group in df3.groupby('ds'):
        # print('权重：',weight_dict[len(group)-1])
        # print('准确率：',(group['ACCURACY'].sum()/len(group))*weight_dict[len(group)-1])
        accuracy_rote += (group['ACCURACY'].sum()/len(group))*weight_dict[len(group)-1]
    df3.to_csv(os.path.join(dataset,f'accuracy_{endtime}.csv'),index=False)
    df4 = pd.DataFrame(columns=['开始日期','结束日期','准确率'])
    df4.loc[len(df4)] = {'开始日期':up_week_dates[0],'结束日期':up_week_dates[-1],'准确率':accuracy_rote}
    df4.to_csv(os.path.join(dataset,f'accuracy_rote_{endtime}.csv'),index=False)
    print(df4)
    # df4.to_sql("accuracy_rote",  con=sqlitedb.connection, if_exists='append', index=False)


end_times = df['CREAT_DATE'].unique()
for endtime in end_times:
    up_week_dates = get_week_date(endtime)
    _get_accuracy_rate(df,up_week_dates,end_time)

# 打印结果



         开始日期        结束日期  准确率
0  2024-11-08  2024-11-15    0
         开始日期        结束日期  准确率
0  2024-11-15  2024-11-22    0
         开始日期        结束日期  准确率
0  2024-11-15  2024-11-22    0
         开始日期        结束日期  准确率
0  2024-11-15  2024-11-22    0
         开始日期        结束日期  准确率
0  2024-11-15  2024-11-22    0
         开始日期        结束日期  准确率
0  2024-11-15  2024-11-22    0
         开始日期        结束日期       准确率
0  2024-11-22  2024-11-29  0.808456
         开始日期        结束日期       准确率
0  2024-11-22  2024-11-29  0.808456
         开始日期        结束日期       准确率
0  2024-11-22  2024-11-29  0.808456
         开始日期        结束日期       准确率
0  2024-11-22  2024-11-29  0.808456
         开始日期        结束日期       准确率
0  2024-11-22  2024-11-29  0.808456
         开始日期        结束日期       准确率
0  2024-11-29  2024-12-06  0.955061
         开始日期        结束日期       准确率
0  2024-11-29  2024-12-06  0.955061
         开始日期        结束日期       准确率
0  2024-11-29  2024-12-06  0.955061
         开始日期        结束日期       准确率
0  2024-11-29  2

In [ ]:
import datetime
# ds 按周取
df['Ds_Week'] = df['ds'].apply(lambda x: x.strftime('%U'))
df['Pre_Week'] = df['PREDICT_DATE'].apply(lambda x: x.strftime('%U'))

In [ ]:
df

ds  ACCURACY PREDICT_DATE  CREAT_DATE  HIGH_PRICE_y  LOW_PRICE_y  \
0  2024-11-26  1.000000   2024-11-26  2024-11-25         73.80        71.63   
1  2024-11-27  1.000000   2024-11-27  2024-11-25         72.85        71.71   
2  2024-11-28  0.789324   2024-11-28  2024-11-25         72.96        71.85   
3  2024-11-29  1.000000   2024-11-29  2024-11-25         73.34        71.75   
4  2024-12-02  0.853412   2024-12-02  2024-11-25         72.89        71.52   
..        ...       ...          ...         ...           ...          ...   
70 2024-11-25  0.118328   2024-11-25  2024-11-22         74.83        72.30   
71 2024-11-26  0.000000   2024-11-26  2024-11-22         73.80        71.63   
72 2024-11-27  0.000000   2024-11-27  2024-11-22         72.85        71.71   
73 2024-11-28  0.000000   2024-11-28  2024-11-22         72.96        71.85   
74 2024-11-29  0.000000   2024-11-29  2024-11-22         73.34        71.75   

    MIN_PRICE  MAX_PRICE Ds_Week Pre_Week  
0   71.071556  76.006900      47       47  
1   71.003624  75.580560      47       47  
2   72.083850  76.204260      47       47  
3   71.329730  75.703950      47       47  
4   71.720825  76.264275      48       48  
..        ...        ...     ...      ...  
70  74.530630  76.673140      47       47  
71  74.440430  76.874565      47       47  
72  74.663180  76.734130      47       47  
73  74.708410  77.141050      47       47  
74  74.703210  77.746170      47       47  

[75 rows x 10 columns]

In [ ]:
# 取结束日期上一周的日期
endtime = '2024-12-3'
endtimeweek = datetime.datetime.strptime(endtime, '%Y-%m-%d')
up_week = endtimeweek - datetime.timedelta(days=endtimeweek.weekday() + 14)
up_week_dates = [up_week + datetime.timedelta(days=i) for i in range(14)][4:-2]
up_week_dates = [date.strftime('%Y-%m-%d') for date in up_week_dates]
print(up_week_dates)


df3 = df.copy()
df3 = df3[df3['CREAT_DATE'].isin(up_week_dates)]
df3 = df3[df3['PREDICT_DATE'].isin(up_week_dates)]
print(df3.shape)
df3.to_csv('up_week_dates.csv',index=False)

['2024-11-22', '2024-11-23', '2024-11-24', '2024-11-25', '2024-11-26', '2024-11-27', '2024-11-28', '2024-11-29']


(15, 10)


In [ ]:
total = len(df3)
accuracy_rote = 0
# for i,group in df3.groupby('CREAT_DATE'):
for i,group in df3.groupby('ds'):
    print(i)
    print('权重：',round(len(group)/total,2))
    print('准确率：',group['ACCURACY'].sum()/(len(group)/total))
    accuracy_rote += group['ACCURACY'].sum()/(len(group)/total)

print(accuracy_rote)

2024-11-25 00:00:00
权重： 0.07
准确率： 1.7749209486165771
2024-11-26 00:00:00
权重： 0.13
准确率： 7.5
2024-11-27 00:00:00
权重： 0.2
准确率： 8.034364035087705
2024-11-28 00:00:00
权重： 0.27
准确率： 9.718006756756724
2024-11-29 00:00:00
权重： 0.33
准确率： 10.824716981132076
37.85200872159308
